In [1]:
# Import libraries
import os
from os import listdir
import geopandas as gpd
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt

import dask.dataframe as dd
import dask_geopandas

c:\Users\uttar\miniforge3\envs\analyzeInfra\Lib\site-packages\dask\dataframe\__init__.py:42: FutureWarning: 
Dask dataframe query planning is disabled because dask-expr is not installed.

You can install it with `pip install dask[dataframe]` or `conda install dask`.
This will raise in a future version.

  warnings.warn(msg, FutureWarning)


### All states except California, Florida, Texas

In [ ]:
# file_path = r"D:\Work\Box Sync\TRB 2024\Extracted_links" 
file_path = r"D:\Work\Box Sync\TRB 2024\Extracted_links\Temporary"
os.chdir(file_path)

# Reading and saving the links data as a dict
links = {}
# iterate through all file
for file in os.listdir():
    # Check whether file is in text format or not
    if file.endswith("link.csv"):
        links[file[:-4]] = pd.read_csv(file, encoding='cp1252')

In [3]:
# # NOT USING THE NODES
# # Reading and saving the nodes data as a dict
# nodes = {}
# # iterate through all file
# for file in os.listdir():
#     # Check whether file is in text format or not
#     if file.endswith("node.csv"):
#         nodes[file[:-4]] = pd.read_csv(file, encoding='cp1252', low_memory=False)

In [4]:
# print(links['utah_link'].shape)
# # Check if there's multiple links for a node pair
# if links['utah_link'].groupby(['from_node_id', 'to_node_id']).size().sum() == links['utah_link'].shape[0]:
#     print('===One link connecting a node pairs===')

In [5]:
print(links.keys())

dict_keys(['south-carolina_link', 'south-dakota_link', 'tennessee_link', 'utah_link', 'vermont_link', 'virginia_link', 'washington_link', 'west-virginia_link', 'wisconsin_link', 'wyoming_link'])


In [6]:
# Exporting all shapefiles for plotting
# Importing the places shapefiles for all states
# combining them into one for further use
from pathlib import Path
# define the file location
folder = Path(r"D:\Work\Box Sync\TRB 2024\US_places_2020\temp\\")
# reading the zip file
shapefiles = folder.glob("tl_2020_*_place.zip")
# combining places for US into one file
gdf = [gpd.read_file(shp) for shp in shapefiles]



In [7]:
len(gdf), type(gdf)

(10, list)

In [ ]:
# # MAKE SURE THAT THESE TWO DICTS ARE ORDERED CORRECTLY TO MAKE THE LOOP WORK
# state_code = ['01','04','05', '08','09','10','11','13','15','16','17','18','19','20','21','22','23','24',
#               '25', '26','27','28','29','30', '31','32','33','34','35','36','37','38','39','40','41','42',
#               '44','45','46','47','49','50','51','53','54','55','56']

# print(len(state_code))

# state_names_gdf = ['alabama_link', 'arizona_link', 'arkansas_link', 'colorado_link', 'connecticut_link', 'delaware_link',
#                    'district-of-columbia_link', 'georgia_link', 'hawaii_link', 'idaho_link', 'illinois_link', 'indiana_link',
#                    'iowa_link', 'kansas_link', 'kentucky_link', 'louisiana_link', 'maine_link', 'maryland_link','massachusetts_link',
#                    'michigan_link', 'minnesota_link', 'mississippi_link', 'missouri_link', 'montana_link', 'nebraska_link', 
#                    'nevada_link', 'new-hampshire_link', 'new-jersey_link', 'new-mexico_link', 'new-york_link', 'north-carolina_link',
#                    'north-dakota_link', 'ohio_link', 'oklahoma_link', 'oregon_link', 'pennsylvania_link', 'rhode-island_link', 
#                    'south-carolina_link', 'south-dakota_link', 'tennessee_link', 'utah_link', 'vermont_link', 'virginia_link', 
#                    'washington_link', 'west-virginia_link', 'wisconsin_link', 'wyoming_link']
                   
# print(len(state_names_gdf))
# place_dict = dict(zip(state_names_gdf, gdf))

# MAKE SURE THAT THESE TWO DICTS ARE ORDERED CORRECTLY TO MAKE THE LOOP WORK
state_code = ['45','46','47','49','50','51','53','54','55','56']

# state_name = links.keys()
# state_dict = dict(zip(state_name, state_code))
print(len(state_code))

state_names_gdf = ['south-carolina_link', 'south-dakota_link', 'tennessee_link', 'utah_link', 'vermont_link', 'virginia_link', 'washington_link', 
                   'west-virginia_link', 'wisconsin_link', 'wyoming_link']
                   
print(len(state_names_gdf))
place_dict = dict(zip(state_names_gdf, gdf))

10
10


In [9]:
# CHECK
if len(links.keys()) != len(gdf):
    print("!!! Lengths do not MATCH !!! CHECK WHETHER SHAPEFILES ALIGN WITH STATE CODES")
else:
    print("Go ahead..")

Go ahead..


In [10]:
import shapely
import geopandas as gpd
from pyproj import CRS
import utm

# Convert df to gdf
# https://stackoverflow.com/questions/71907567/valueerror-geodataframe-does-not-support-multiple-columns-using-the-geometry-co
# Coordinate system of osm: http://download.geofabrik.de/osm-data-in-gis-formats-free.pdf
# must have a geometry column in csv
def csv_2_gdf(df):
    gdf = gpd.GeoDataFrame(df.loc[:, [c for c in df.columns if c != "geometry"]], 
                           geometry=gpd.GeoSeries.from_wkt(df["geometry"]),
                           crs="epsg:4326",)
    return gdf

# assign utm based on the lat long value of a geometry
def utm_crs_from_latlon(lat, lon):
    crs_params = dict(
        proj = 'utm',
        zone = utm.latlon_to_zone_number(lat, lon),
        south = lat < 0
        )
    return CRS.from_dict(crs_params)

# Get projected geometry to create buffer for place polygons
def get_utm_projected(geom_wkt): # geom is shapely geometry file
    geom_shape = shapely.wkt.loads(geom_wkt)
    utm_crs = utm_crs_from_latlon(lat = geom_shape.centroid.y, lon = geom_shape.centroid.x)
    # print(utm_crs)
    line_geo = gpd.GeoSeries([geom_shape], crs='EPSG:4326')
    # taking a buffer of 3.6 meters to include th roads along the periphery
    return line_geo.to_crs(utm_crs).buffer(3.6)

# reads link files from a list of link dataframes for each place
def read_osm_links(key):
    state_streets = csv_2_gdf(links[key]) # 'alabama_link'
    # 7, 8, 11 = living street, service road, track
    #  Track roads are not maintained by the city or state for traffic to travel on.
    # Service roads are privately maintained
    # https://www.fhwa.dot.gov/ohim/onh00/onh2p5.htm#:~:text=Collectors:%20The%20collectors%20provide%20both,town%2C%20city%2C%20county).
    # The vast majority (77.4%) of the Nation's roadways are owned by units of local government (town, city, county).
    state_streets_major = state_streets[(state_streets['link_type'] < 16)]
    # Create a new column with sorted tuples
    state_streets_major['sorted_nodes'] = list(zip(state_streets_major['from_node_id'], state_streets_major['to_node_id']))
    state_streets_major['sorted_nodes'] = state_streets_major['sorted_nodes'].apply(lambda x: tuple(sorted(x)))
    return state_streets_major


def fill_lanes_with_median_or_one(df, lanes_col='lanes', link_type_col='link_type'):
    # Ensure that lanes_col and link_type_col exist in the dataframe
    if lanes_col not in df.columns or link_type_col not in df.columns:
        raise ValueError(f"Columns {lanes_col} or {link_type_col} not found in the dataframe.")
    
    # Define a function that fills NaN values with the median or 1 if the median is not found
    def fill_na_with_median(group):
        median_value = group[lanes_col].median()
        # If the median value is NaN (all NaN lanes in the group), replace NaN with 1
        if pd.isna(median_value):
            group[lanes_col].fillna(1, inplace=True)
        else:
            group[lanes_col].fillna(median_value, inplace=True)
        return group
    
    # Apply the function to each group defined by the 'link_type' column
    df = df.groupby(link_type_col).apply(fill_na_with_median).reset_index(drop=True)
    
    return df

def custom_agg(series):
    """
    Custom aggregation function:
    - If the number of elements is 4, compute the sum and divide by 2.
    - Otherwise, compute the mean.
    """
    n = len(series)
    if n == 4:
        return series.sum() / 2
    else:
        return series.mean()


In [11]:
geoids = []
name_of_places = []
clipped_to_places = []

# clipping roads at state level to places 
for key in links.keys():
    print(key)
    state_streets_major = read_osm_links(key)      
    state_places = place_dict[key]

    geoids.append(state_places.GEOID)
    name_of_places.append(state_places.NAMELSAD)
    gdf_wkt = state_places.geometry.to_wkt()
    
    # Clip link gdf by multipolygons
    # Creates a list of clipped files per place in states_places
    clipped_streets = [gpd.clip(state_streets_major, get_utm_projected(geom_wkt).to_crs(state_streets_major.crs)) for geom_wkt in gdf_wkt]
    clipped_to_places.append(clipped_streets)

print(len(clipped_to_places))

south-carolina_link


c:\Users\uttar\miniforge3\envs\analyzeInfra\Lib\site-packages\geopandas\geodataframe.py:1543: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  super().__setitem__(key, value)


south-dakota_link


c:\Users\uttar\miniforge3\envs\analyzeInfra\Lib\site-packages\geopandas\geodataframe.py:1543: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  super().__setitem__(key, value)


tennessee_link


...

wisconsin_link


c:\Users\uttar\miniforge3\envs\analyzeInfra\Lib\site-packages\geopandas\geodataframe.py:1543: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  super().__setitem__(key, value)


wyoming_link


c:\Users\uttar\miniforge3\envs\analyzeInfra\Lib\site-packages\geopandas\geodataframe.py:1543: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  super().__setitem__(key, value)


10


In [12]:
# # deomo
# X = clipped_to_places[0][0]
# x = dg.from_geopandas(X, npartitions=4)
# utm_length = []
# crs_length = []
# # convert geodataframe geometry to wkt format
# gdf_wkt = x.geometry.to_wkt()
# for geom in gdf_wkt:
#     # # Convert to accurate UTM: https://gis.stackexchange.com/questions/436938/calculate-length-using-geopandas
#     # read geometry as a shapely geometry
#     line_shape = shapely.wkt.loads(geom)
#     # indentify the centroid of the geometry
#     utm_crs = utm_crs_from_latlon(lat = line_shape.centroid.y,
#                                     lon = line_shape.centroid.x)       

#     line_geo = gpd.GeoSeries([line_shape], crs='EPSG:4326')
#     crs_length.append(line_geo.to_crs('EPSG:3857').length.values)
#     utm_length.append(line_geo.to_crs(utm_crs).length.values)
# output_df = pd.DataFrame(x)
# output_df['utm_length'] = utm_length
# output_df['crs_length'] = crs_length


# output_df_filled = fill_lanes_with_median_or_one(output_df)
# # Filter the data and calculate the sum of road lengths for each road type 
# output_df_filled['utm_length'] = output_df_filled['utm_length'].astype(str).str.replace("[","").str.replace("]","").astype(float)
# output_df_filled['crs_length'] = output_df_filled['crs_length'].astype(str).str.replace("[","").str.replace("]","").astype(float)
# output_df_filled['lane_m_utm_length'] = output_df_filled['utm_length'] * output_df_filled['lanes']
                      
# road_lengths = output_df_filled[output_df_filled['allowed_uses'].str.contains('auto')].groupby('link_type_name')['utm_length'].sum()
# cl_road_lengths = output_df_filled[output_df_filled['allowed_uses'].str.contains('auto')].groupby(['link_type_name', 'sorted_nodes', 'utm_length']).agg({'utm_length':'mean'}).groupby('link_type_name').sum()
# lane_road_lengths = output_df_filled[output_df_filled['allowed_uses'].str.contains('auto')].groupby('link_type_name')['lane_m_utm_length'].sum()
# non_auto_rl = output_df_filled[~output_df_filled['allowed_uses'].str.contains('auto')].groupby('link_type_name')['lane_m_utm_length'].sum()
# non_auto_cl_rl = output_df_filled[~output_df_filled['allowed_uses'].str.contains('auto')].groupby(['link_type_name', 'sorted_nodes', 'utm_length']).agg({'utm_length':'mean'}).groupby('link_type_name').sum()
# non_auto_lane_rl = output_df_filled[~output_df_filled['allowed_uses'].str.contains('auto')].groupby('link_type_name')['lane_m_utm_length'].sum()
# # print(cl_road_lengths)
# cl_road_lengths = cl_road_lengths.squeeze(axis=1)
# non_auto_cl_rl  = non_auto_cl_rl.squeeze(axis=1)

# X0 = output_df_filled.groupby(['sorted_nodes','utm_length']).size().reset_index()
# X0
# # X[X[0]>2]
# # output_df_filled[output_df_filled['sorted_nodes'] ==(349285, 350145)]

In [ ]:
no_roads = []
name_no_roads = []

for i, state_clipped in enumerate(clipped_to_places):
    clipped_projected_lengths = []
    for j, clipped in enumerate(state_clipped):
        # print(j)
        clipped = clipped[~clipped.is_empty]
        if clipped.shape[0] != 0:
            print(f'Shape of the roadway clipped by place at index {j} for state {i} is {clipped.shape}')
            output_df = pd.DataFrame(clipped)
            utm_length = []
            crs_length = []
            # convert geodataframe geometry to wkt format
            gdf_wkt = clipped.geometry.to_wkt()
            for geom in gdf_wkt:
                # # Convert to accurate UTM: https://gis.stackexchange.com/questions/436938/calculate-length-using-geopandas
                # read geometry as a shapely geometry
                line_shape = shapely.wkt.loads(geom)
                # indentify the centroid of the geometry
                utm_crs = utm_crs_from_latlon(lat = line_shape.centroid.y,
                                              lon = line_shape.centroid.x)       

                line_geo = gpd.GeoSeries([line_shape], crs='EPSG:4326')
                crs_length.append(line_geo.to_crs('EPSG:3857').length.values)
                utm_length.append(line_geo.to_crs(utm_crs).length.values)

            if output_df.shape[0] == len(utm_length):
                try:
                    output_df['utm_length'] = utm_length
                    output_df['crs_length'] = crs_length
                except Exception as e:        
                    print(f"!!!====== ERROR ======!!! :\n  {file}")
                    print(f"!!!File shapes do not match!!\n")
                    continue

            clipped_projected_lengths.append(output_df)

        else:
            print('Places and geoids with missing geometry, so no x y values:====')
            print(geoids[i][j], name_of_places[i][j])
            no_roads.append(geoids[i][j])
            name_no_roads.append(name_of_places[i][j])
            # remove element at index i from the geoid list
            geoids[i].pop(j)
            name_of_places[i].pop(j)
    
    print(len(clipped_projected_lengths))

    error_opening = []

    # print(clipped_projected_lengths)

    motorway_roads = []
    trunk_roads = []
    primary_roads = []
    secondary_roads = []
    tertiary_roads = []
    unclassified_roads = []
    residential_roads = []
    service_roads = [] 
    track_roads = []
    footway_roads = []
    cycleway_roads = []
    living_street = []

    cl_motorway_roads = []
    cl_trunk_roads = []
    cl_primary_roads = []
    cl_secondary_roads = []
    cl_tertiary_roads = []
    cl_unclassified_roads = []
    cl_residential_roads = []
    cl_service_roads = [] 
    cl_track_roads = []
    cl_footway_roads = []
    cl_cycleway_roads = []
    cl_living_street = []

    lane_motorway_roads = []
    lane_trunk_roads = []
    lane_primary_roads = []
    lane_secondary_roads = []
    lane_tertiary_roads = []
    lane_unclassified_roads = []
    lane_residential_roads = []
    lane_service_roads = [] 
    lane_track_roads = []
    lane_footway_roads = []
    lane_cycleway_roads = []
    lane_living_street = []

    n_motorway_roads = []
    n_trunk_roads = []
    n_primary_roads = []
    n_secondary_roads = []
    n_tertiary_roads = []
    n_unclassified_roads = []
    n_residential_roads = []
    n_service_roads = [] 
    n_track_roads = []
    n_footway_roads = []
    n_cycleway_roads = []
    n_living_street = []

    n_cl_motorway_roads = []
    n_cl_trunk_roads = []
    n_cl_primary_roads = []
    n_cl_secondary_roads = []
    n_cl_tertiary_roads = []
    n_cl_unclassified_roads = []
    n_cl_residential_roads = []
    n_cl_service_roads = [] 
    n_cl_track_roads = []
    n_cl_footway_roads = []
    n_cl_cycleway_roads = []
    n_cl_living_street = []

    n_lane_motorway_roads = []
    n_lane_trunk_roads = []
    n_lane_primary_roads = []
    n_lane_secondary_roads = []
    n_lane_tertiary_roads = []
    n_lane_unclassified_roads = []
    n_lane_residential_roads = []
    n_lane_service_roads = [] 
    n_lane_track_roads = []
    n_lane_footway_roads = []
    n_lane_cycleway_roads = []
    n_lane_living_street = []

    for k, clipped_links in enumerate(clipped_projected_lengths):
        try:
            clipped_links_w_lanes = fill_lanes_with_median_or_one(clipped_links)
            # Filter the data and calculate the sum of road lengths for each road type 
            clipped_links_w_lanes['utm_length'] = clipped_links_w_lanes['utm_length'].astype(str).str.replace("[","").str.replace("]","").astype(float)
            clipped_links_w_lanes['crs_length'] = clipped_links_w_lanes['crs_length'].astype(str).str.replace("[","").str.replace("]","").astype(float)
            clipped_links_w_lanes['lane_m_utm'] = clipped_links_w_lanes['utm_length'] * clipped_links_w_lanes['lanes']
                                
            road_lengths      = clipped_links_w_lanes[clipped_links_w_lanes['allowed_uses'].str.contains('auto')].groupby('link_type_name')['utm_length'].sum()
            cl_road_lengths   = clipped_links_w_lanes[clipped_links_w_lanes['allowed_uses'].str.contains('auto')].groupby(['link_type_name', 'sorted_nodes', 'utm_length'])['utm_length'].agg(custom_agg).groupby('link_type_name').sum()
            lane_road_lengths = clipped_links_w_lanes[clipped_links_w_lanes['allowed_uses'].str.contains('auto')].groupby('link_type_name')['lane_m_utm'].sum()
            
            non_auto_rl       = clipped_links_w_lanes[~clipped_links_w_lanes['allowed_uses'].str.contains('auto')].groupby('link_type_name')['utm_length'].sum()
            non_auto_cl_rl    = clipped_links_w_lanes[~clipped_links_w_lanes['allowed_uses'].str.contains('auto')].groupby(['link_type_name', 'sorted_nodes', 'utm_length'])['utm_length'].agg(custom_agg).groupby('link_type_name').sum()
            non_auto_lane_rl  = clipped_links_w_lanes[~clipped_links_w_lanes['allowed_uses'].str.contains('auto')].groupby('link_type_name')['lane_m_utm'].sum()
            # print(cl_road_lengths)
            # cl_road_lengths = cl_road_lengths.squeeze(axis=1)
            # non_auto_cl_rl  = non_auto_cl_rl.squeeze(axis=1)

            
            # Append the calculated road lengths to the respective lists
            motorway_roads.append(road_lengths.get('motorway', 0))
            trunk_roads.append(road_lengths.get('trunk', 0))
            primary_roads.append(road_lengths.get('primary', 0))
            secondary_roads.append(road_lengths.get('secondary', 0))
            tertiary_roads.append(road_lengths.get('tertiary', 0))
            unclassified_roads.append(road_lengths.get('unclassified', 0))
            residential_roads.append(road_lengths.get('residential', 0))
            service_roads.append(road_lengths.get('service', 0))
            track_roads.append(road_lengths.get('track', 0))
            footway_roads.append(road_lengths.get('footway', 0))
            cycleway_roads.append(road_lengths.get('cycleway', 0))
            living_street.append(road_lengths.get('living_street', 0))

            cl_motorway_roads.append(cl_road_lengths.get('motorway', 0))
            cl_trunk_roads.append(cl_road_lengths.get('trunk', 0))
            cl_primary_roads.append(cl_road_lengths.get('primary', 0))
            cl_secondary_roads.append(cl_road_lengths.get('secondary', 0))
            cl_tertiary_roads.append(cl_road_lengths.get('tertiary', 0))
            cl_unclassified_roads.append(cl_road_lengths.get('unclassified', 0))
            cl_residential_roads.append(cl_road_lengths.get('residential', 0))
            cl_service_roads.append(cl_road_lengths.get('service', 0))
            cl_track_roads.append(cl_road_lengths.get('track', 0))
            cl_footway_roads.append(cl_road_lengths.get('footway', 0))
            cl_cycleway_roads.append(cl_road_lengths.get('cycleway', 0))
            cl_living_street.append(cl_road_lengths.get('living_street', 0))
            # print("finished upto ", str(k))

            lane_motorway_roads.append(lane_road_lengths.get('motorway', 0))
            lane_trunk_roads.append(lane_road_lengths.get('trunk', 0))
            lane_primary_roads.append(lane_road_lengths.get('primary', 0))
            lane_secondary_roads.append(lane_road_lengths.get('secondary', 0))
            lane_tertiary_roads.append(lane_road_lengths.get('tertiary', 0))
            lane_unclassified_roads.append(lane_road_lengths.get('unclassified', 0))
            lane_residential_roads.append(lane_road_lengths.get('residential', 0))
            lane_service_roads.append(lane_road_lengths.get('service', 0))
            lane_track_roads.append(lane_road_lengths.get('track', 0))
            lane_footway_roads.append(lane_road_lengths.get('footway', 0))
            lane_cycleway_roads.append(lane_road_lengths.get('cycleway', 0))
            lane_living_street.append(lane_road_lengths.get('living_street', 0))

            n_motorway_roads.append(non_auto_rl.get('motorway', 0))
            n_trunk_roads.append(non_auto_rl.get('trunk', 0))
            n_primary_roads.append(non_auto_rl.get('primary', 0))
            n_secondary_roads.append(non_auto_rl.get('secondary', 0))
            n_tertiary_roads.append(non_auto_rl.get('tertiary', 0))
            n_unclassified_roads.append(non_auto_rl.get('unclassified', 0))
            n_residential_roads.append(non_auto_rl.get('residential', 0))
            n_service_roads.append(non_auto_rl.get('service', 0))
            n_track_roads.append(non_auto_rl.get('track', 0))
            n_footway_roads.append(non_auto_rl.get('footway', 0))
            n_cycleway_roads.append(non_auto_rl.get('cycleway', 0))
            n_living_street.append(non_auto_rl.get('living_street', 0))

            n_cl_motorway_roads.append(non_auto_cl_rl.get('motorway', 0))
            n_cl_trunk_roads.append(non_auto_cl_rl.get('trunk', 0))
            n_cl_primary_roads.append(non_auto_cl_rl.get('primary', 0))
            n_cl_secondary_roads.append(non_auto_cl_rl.get('secondary', 0))
            n_cl_tertiary_roads.append(non_auto_cl_rl.get('tertiary', 0))
            n_cl_unclassified_roads.append(non_auto_cl_rl.get('unclassified', 0))
            n_cl_residential_roads.append(non_auto_cl_rl.get('residential', 0))
            n_cl_service_roads.append(non_auto_cl_rl.get('service', 0))
            n_cl_track_roads.append(non_auto_cl_rl.get('track', 0))
            n_cl_footway_roads.append(non_auto_cl_rl.get('footway', 0))
            n_cl_cycleway_roads.append(non_auto_cl_rl.get('cycleway', 0))
            n_cl_living_street.append(non_auto_cl_rl.get('living_street', 0))
            # print("finished upto ", str(k))

            n_lane_motorway_roads.append(non_auto_lane_rl.get('motorway', 0))
            n_lane_trunk_roads.append(non_auto_lane_rl.get('trunk', 0))
            n_lane_primary_roads.append(non_auto_lane_rl.get('primary', 0))
            n_lane_secondary_roads.append(non_auto_lane_rl.get('secondary', 0))
            n_lane_tertiary_roads.append(non_auto_lane_rl.get('tertiary', 0))
            n_lane_unclassified_roads.append(non_auto_lane_rl.get('unclassified', 0))
            n_lane_residential_roads.append(non_auto_lane_rl.get('residential', 0))
            n_lane_service_roads.append(non_auto_lane_rl.get('service', 0))
            n_lane_track_roads.append(non_auto_lane_rl.get('track', 0))
            n_lane_footway_roads.append(non_auto_lane_rl.get('footway', 0))
            n_lane_cycleway_roads.append(non_auto_lane_rl.get('cycleway', 0))
            n_lane_living_street.append(non_auto_lane_rl.get('living_street', 0))
               
        except Exception as e:
            error_opening.append(clipped_links.index)
            print(f"Error opening file clipped_links at position {k} of clipped_projected_lengths: {e}")

    list_of_tuples = list(zip(geoids[i], name_of_places[i], motorway_roads, trunk_roads, primary_roads, secondary_roads, 
                          tertiary_roads, unclassified_roads, residential_roads, service_roads, track_roads, footway_roads,
                          cycleway_roads, living_street, cl_motorway_roads, cl_trunk_roads, cl_primary_roads,
                          cl_secondary_roads, cl_tertiary_roads, cl_unclassified_roads, cl_residential_roads,
                          cl_service_roads, cl_track_roads, cl_footway_roads, cl_cycleway_roads, cl_living_street,
                          lane_motorway_roads, lane_trunk_roads, lane_primary_roads, lane_secondary_roads, lane_tertiary_roads,
                          lane_unclassified_roads, lane_residential_roads, lane_service_roads, lane_track_roads, lane_footway_roads,
                          lane_cycleway_roads, lane_living_street, n_motorway_roads, n_trunk_roads, n_primary_roads, n_secondary_roads,
                          n_tertiary_roads, n_unclassified_roads, n_residential_roads, n_service_roads, n_track_roads, n_footway_roads, 
                          n_cycleway_roads, n_living_street,n_cl_motorway_roads, n_cl_trunk_roads, n_cl_primary_roads, n_cl_secondary_roads, 
                          n_cl_tertiary_roads, n_cl_unclassified_roads, n_cl_residential_roads, n_cl_service_roads, n_cl_track_roads,
                          n_cl_footway_roads, n_cl_cycleway_roads, n_cl_living_street, n_lane_motorway_roads, n_lane_trunk_roads, 
                          n_lane_primary_roads, n_lane_secondary_roads, n_lane_tertiary_roads, n_lane_unclassified_roads, n_lane_residential_roads,
                          n_lane_service_roads, n_lane_track_roads, n_lane_footway_roads, n_lane_cycleway_roads, n_lane_living_street))
    
    df_roads = pd.DataFrame(list_of_tuples, columns = ['GEOID', 'NAMELSAD','motorway', 'trunk', 'primary', 'secondary', 'tertiary', 'unclassified', 'residential',
                                                       'service', 'track', 'footway', 'cycleway', 'living_street', 
                                                       'cl_motorway', 'cl_trunk', 'cl_primary', 'cl_secondary', 'cl_tertiary', 'cl_unclassified', 'cl_residential',
                                                       'cl_service', 'cl_track', 'cl_footway', 'cl_cycleway', 'cl_living_street',
                                                       'lane_m_motorway', 'lane_m_trunk', 'lane_m_primary', 'lane_m_secondary', 'lane_m_tertiary', 
                                                       'lane_m_unclassified', 'lane_m_residential', 'lane_m_service', 'lane_m_track', 'lane_m_footway',
                                                       'lane_m_cycleway', 'lane_m_living_street',
                                                       'n_motorway', 'n_trunk', 'n_primary', 'n_secondary', 'n_tertiary', 'n_unclassified', 'n_residential',
                                                       'n_service', 'n_track', 'n_footway', 'n_cycleway', 'n_living_street', 
                                                       'n_cl_motorway', 'n_cl_trunk', 'n_cl_primary', 'n_cl_secondary', 'n_cl_tertiary', 'n_cl_unclassified', 'n_cl_residential',
                                                       'n_cl_service', 'n_cl_track', 'n_cl_footway', 'n_cl_cycleway', 'n_cl_living_street',
                                                       'n_lane_m_motorway', 'n_lane_m_trunk', 'n_lane_m_primary', 'n_lane_m_secondary', 'n_lane_m_tertiary', 
                                                       'n_lane_m_unclassified', 'n_lane_m_residential', 'n_lane_m_service', 'n_lane_m_track', 'n_lane_m_footway',
                                                       'n_lane_m_cycleway', 'n_lane_m_living_street'])

    print(df_roads.shape)
    df_roads.to_csv(r'E:\Scripts\project_QI\data\osm\All states\df_roads_utm_'+ str(i) + '.csv')

Shape of the roadway clipped by place at index 0 for state 0 is (58, 19)
Shape of the roadway clipped by place at index 1 for state 0 is (1457, 19)
Shape of the roadway clipped by place at index 2 for state 0 is (206, 19)
Shape of the roadway clipped by place at index 3 for state 0 is (681, 19)
Shape of the roadway clipped by place at index 4 for state 0 is (237, 19)
Shape of the roadway clipped by place at index 5 for state 0 is (470, 19)
Shape of the roadway clipped by place at index 6 for state 0 is (2270, 19)
Shape of the roadway clipped by place at index 7 for state 0 is (2678, 19)
Shape of the roadway clipped by place at index 8 for state 0 is (2401, 19)
Shape of the roadway clipped by place at index 9 for state 0 is (116, 19)
Shape of the roadway clipped by place at index 10 for state 0 is (4594, 19)
Shape of the roadway clipped by place at index 11 for state 0 is (1214, 19)
Shape of the roadway clipped by place at index 12 for state 0 is (75, 19)
Shape of the roadway clipped by

c:\Users\uttar\miniforge3\envs\analyzeInfra\Lib\site-packages\numpy\lib\nanfunctions.py:1215: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
c:\Users\uttar\miniforge3\envs\analyzeInfra\Lib\site-packages\numpy\lib\nanfunctions.py:1215: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
c:\Users\uttar\miniforge3\envs\analyzeInfra\Lib\site-packages\numpy\lib\nanfunctions.py:1215: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
c:\Users\uttar\miniforge3\envs\analyzeInfra\Lib\site-packages\numpy\lib\nanfunctions.py:1215: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
c:\Users\uttar\miniforge3\envs\analyzeInfra\Lib\site-packages\numpy\lib\nanfunctions.py:1215: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
c:\Users\uttar\miniforge3\envs\analyzeInfra\Lib\site-packages\num

(475, 74)
Shape of the roadway clipped by place at index 0 for state 1 is (190, 19)
Shape of the roadway clipped by place at index 1 for state 1 is (78, 19)
Shape of the roadway clipped by place at index 2 for state 1 is (752, 19)
Shape of the roadway clipped by place at index 3 for state 1 is (265, 19)
Shape of the roadway clipped by place at index 4 for state 1 is (737, 19)
Shape of the roadway clipped by place at index 5 for state 1 is (142, 19)
Shape of the roadway clipped by place at index 6 for state 1 is (295, 19)
Shape of the roadway clipped by place at index 7 for state 1 is (1746, 19)
Shape of the roadway clipped by place at index 8 for state 1 is (310, 19)
Shape of the roadway clipped by place at index 9 for state 1 is (155, 19)
Shape of the roadway clipped by place at index 10 for state 1 is (313, 19)
Shape of the roadway clipped by place at index 11 for state 1 is (64, 19)
Shape of the roadway clipped by place at index 12 for state 1 is (344, 19)
Shape of the roadway clipp

c:\Users\uttar\miniforge3\envs\analyzeInfra\Lib\site-packages\numpy\lib\nanfunctions.py:1215: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
c:\Users\uttar\miniforge3\envs\analyzeInfra\Lib\site-packages\numpy\lib\nanfunctions.py:1215: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
c:\Users\uttar\miniforge3\envs\analyzeInfra\Lib\site-packages\numpy\lib\nanfunctions.py:1215: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
c:\Users\uttar\miniforge3\envs\analyzeInfra\Lib\site-packages\numpy\lib\nanfunctions.py:1215: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
c:\Users\uttar\miniforge3\envs\analyzeInfra\Lib\site-packages\numpy\lib\nanfunctions.py:1215: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
c:\Users\uttar\miniforge3\envs\analyzeInfra\Lib\site-packages\num

(486, 74)
Shape of the roadway clipped by place at index 0 for state 2 is (172, 19)
Shape of the roadway clipped by place at index 1 for state 2 is (220, 19)
Shape of the roadway clipped by place at index 2 for state 2 is (2462, 19)
Shape of the roadway clipped by place at index 3 for state 2 is (5664, 19)
Shape of the roadway clipped by place at index 4 for state 2 is (15542, 19)
Shape of the roadway clipped by place at index 5 for state 2 is (1920, 19)
Shape of the roadway clipped by place at index 6 for state 2 is (5825, 19)
Shape of the roadway clipped by place at index 7 for state 2 is (523, 19)
Shape of the roadway clipped by place at index 8 for state 2 is (2743, 19)
Shape of the roadway clipped by place at index 9 for state 2 is (1043, 19)
Shape of the roadway clipped by place at index 10 for state 2 is (16563, 19)
Shape of the roadway clipped by place at index 11 for state 2 is (2575, 19)
Shape of the roadway clipped by place at index 12 for state 2 is (1784, 19)
Shape of the 

...

(439, 74)
Shape of the roadway clipped by place at index 0 for state 8 is (255, 19)
Shape of the roadway clipped by place at index 1 for state 8 is (230, 19)
Shape of the roadway clipped by place at index 2 for state 8 is (98, 19)
Shape of the roadway clipped by place at index 3 for state 8 is (4374, 19)
Shape of the roadway clipped by place at index 4 for state 8 is (5905, 19)
Shape of the roadway clipped by place at index 5 for state 8 is (741, 19)
Shape of the roadway clipped by place at index 6 for state 8 is (283, 19)
Shape of the roadway clipped by place at index 7 for state 8 is (174, 19)
Shape of the roadway clipped by place at index 8 for state 8 is (1180, 19)
Shape of the roadway clipped by place at index 9 for state 8 is (102, 19)
Shape of the roadway clipped by place at index 10 for state 8 is (397, 19)
Shape of the roadway clipped by place at index 11 for state 8 is (301, 19)
Shape of the roadway clipped by place at index 12 for state 8 is (500, 19)
Shape of the roadway cl

c:\Users\uttar\miniforge3\envs\analyzeInfra\Lib\site-packages\numpy\lib\nanfunctions.py:1215: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
c:\Users\uttar\miniforge3\envs\analyzeInfra\Lib\site-packages\numpy\lib\nanfunctions.py:1215: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
c:\Users\uttar\miniforge3\envs\analyzeInfra\Lib\site-packages\numpy\lib\nanfunctions.py:1215: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
c:\Users\uttar\miniforge3\envs\analyzeInfra\Lib\site-packages\numpy\lib\nanfunctions.py:1215: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
c:\Users\uttar\miniforge3\envs\analyzeInfra\Lib\site-packages\numpy\lib\nanfunctions.py:1215: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
c:\Users\uttar\miniforge3\envs\analyzeInfra\Lib\site-packages\num

(804, 74)
Shape of the roadway clipped by place at index 0 for state 9 is (1124, 19)
Shape of the roadway clipped by place at index 1 for state 9 is (246, 19)
Shape of the roadway clipped by place at index 2 for state 9 is (211, 19)
Shape of the roadway clipped by place at index 3 for state 9 is (6865, 19)
Shape of the roadway clipped by place at index 4 for state 9 is (2760, 19)
Shape of the roadway clipped by place at index 5 for state 9 is (1162, 19)
Shape of the roadway clipped by place at index 6 for state 9 is (613, 19)
Shape of the roadway clipped by place at index 7 for state 9 is (186, 19)
Shape of the roadway clipped by place at index 8 for state 9 is (1473, 19)
Shape of the roadway clipped by place at index 9 for state 9 is (122, 19)
Shape of the roadway clipped by place at index 10 for state 9 is (2144, 19)
Shape of the roadway clipped by place at index 11 for state 9 is (6961, 19)
Shape of the roadway clipped by place at index 12 for state 9 is (983, 19)
Shape of the roadw

c:\Users\uttar\miniforge3\envs\analyzeInfra\Lib\site-packages\numpy\lib\nanfunctions.py:1215: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
c:\Users\uttar\miniforge3\envs\analyzeInfra\Lib\site-packages\numpy\lib\nanfunctions.py:1215: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
c:\Users\uttar\miniforge3\envs\analyzeInfra\Lib\site-packages\numpy\lib\nanfunctions.py:1215: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
c:\Users\uttar\miniforge3\envs\analyzeInfra\Lib\site-packages\numpy\lib\nanfunctions.py:1215: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
c:\Users\uttar\miniforge3\envs\analyzeInfra\Lib\site-packages\numpy\lib\nanfunctions.py:1215: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
c:\Users\uttar\miniforge3\envs\analyzeInfra\Lib\site-packages\num

(205, 74)


In [14]:
missing_places = {no_roads[i]: name_no_roads[i] for i in range(len(no_roads))}
print(len(missing_places))
missing_places

0


{}

In [15]:
# {'0405450': 'Bear Flat CDP', 
#  '0812030': 'Carbonate town',
#  '3703150': 'Bald Head Island village',
#  '4641548': 'Mayfield Colony CDP',
#  '4650310': 'Platte Colony CDP
# }

In [16]:
# pd.set_option('display.max_colwidth', None)

In [17]:
# count=0
# clipped_x = clipped_to_places[0][58]
# clipped_y = clipped_x[~clipped_x.is_empty]
# gdf_wkt = clipped_y.geometry.to_wkt()
# for geom in gdf_wkt:
#     # # Convert to accurate UTM: https://gis.stackexchange.com/questions/436938/calculate-length-using-geopandas
#     # print(geom)
#     # read geometry as a shapely geometry
#     line_shape = shapely.wkt.loads(geom)
#     if line_shape.is_empty:
#         print('empty geom')
#     else:
#         # indentify the centroid of the geometry
#         utm_crs = utm_crs_from_latlon(lat = line_shape.centroid.y,
#                                     lon = line_shape.centroid.x)       

#         line_geo = gpd.GeoSeries([line_shape], crs='EPSG:4326')
#         print(line_geo.to_crs('EPSG:3857').length.values)
#         print(line_geo.to_crs(utm_crs).length.values)
#         count = count+1
#         print(count)

In [18]:
# import dask.dataframe as dd
# import dask_geopandas as dgpd
# import geopandas as gpd
# import shapely.wkt

# def csv_2_gdf_dask(df):
#     # Convert the pandas DataFrame to a Dask DataFrame
#     ddf = dd.from_pandas(df, npartitions=4)
    
#     # Convert the 'geometry' column to a Dask GeoSeries
#     geometry = dgpd.from_geopandas(gpd.GeoSeries.from_wkt(df["geometry"]), npartitions=4)
    
#     # Create a Dask GeoDataFrame without specifying the CRS
#     dgdf = dgpd.from_dask_dataframe(ddf, geometry=geometry)
    
#     # Set the CRS separately
#     dgdf = dgdf.set_crs("epsg:4326")
    
#     return dgdf

# # Reads link files from a list of link dataframes for each place
# def read_osm_links_dask(key):
#     state_streets = csv_2_gdf_dask(links[key])  # 'alabama_link'
#     state_streets_major = state_streets[state_streets['link_type'] < 16]
    
#     # Create a new column with sorted tuples using map_partitions
#     state_streets_major['sorted_nodes'] = state_streets_major.map_partitions(
#         lambda df: list(zip(df['from_node_id'], df['to_node_id'])), meta=('sorted_nodes', object)
#     )
#     state_streets_major['sorted_nodes'] = state_streets_major['sorted_nodes'].map_partitions(
#         lambda col: col.apply(lambda x: tuple(sorted(x))), meta=('sorted_nodes', object)
#     )
    
#     return state_streets_major

# def get_utm_projected_dask(geom_wkt):  # geom is shapely geometry file
#     geom_shape = shapely.wkt.loads(geom_wkt)
#     utm_crs = utm_crs_from_latlon(lat=geom_shape.centroid.y, lon=geom_shape.centroid.x)
    
#     # Create a GeoSeries and convert it to a Dask GeoSeries
#     line_geo0 = gpd.GeoSeries([geom_shape], crs='EPSG:4326')
#     line_geo = dgpd.from_geopandas(line_geo0, npartitions=4)

#     # Taking a buffer of 3.6 meters to include the roads along the periphery
#     buffered_geo = line_geo.to_crs(utm_crs).buffer(3.6)
    
#     # Convert the buffered GeoSeries back to GeoDataFrame
#     buffered_gdf = gpd.GeoDataFrame(geometry=buffered_geo, crs=utm_crs)
    
#     return buffered_gdf

# # Example usage
# # geom_wkt = "your WKT string here"
# # result = get_utm_projected_dask(geom_wkt)

# geoids = []
# name_of_places = []
# clipped_to_places = []

# # clipping roads at state level to places 
# for key in links.keys():
#     print(key)
#     state_streets_major = read_osm_links_dask(key)      
#     state_places = place_dict[key]
#     # state_places = dg.from_geopandas(state_places0, npartitions=4)

#     geoids.append(state_places.GEOID)
#     name_of_places.append(state_places.NAMELSAD)
#     gdf_wkt = state_places.geometry.to_wkt()
    
#     # Clip link gdf by multipolygons
#     # Creates a list of clipped files per place in states_places
#     clipped_streets = [gpd.clip(state_streets_major.compute(), get_utm_projected_dask(geom_wkt).to_crs(state_streets_major.crs)) for geom_wkt in gdf_wkt]
#     clipped_to_places.append(clipped_streets)

# print(len(clipped_to_places))
